In [6]:
import pandas as pd                
from scipy.stats import iqr
import matplotlib.pyplot as plt
import seaborn as sns
from sklearn.ensemble import IsolationForest

In [2]:
# Define IQR function
def IQR(column): 
    q25, q75 = column.quantile([0.25, 0.75])
    return q75-q25

In [3]:
# Function to calculate tidal statistics

def tidal_stats(data):
    try:
        # set root_url to github path with data
        root_url = 'https://github.com/MyreLab/thames-tidal-variation/raw/main/datasets/' 

        # Load datasets
        df = pd.read_csv(root_url+data) 

        # Take only the first three columns
        df = df.iloc[:, :3]

        # Rename columns
        df.columns = ['datetime', 'water_level', 'is_high_tide']

        # Convert to datetime
        df['datetime'] = pd.to_datetime(df['datetime'])

        # Convert to float
        df['water_level'] = df.water_level.astype(float)

        # Create extra month and year columns for easy access
        df['month'] = df['datetime'].dt.month
        df['year'] = df['datetime'].dt.year

        # Filter df for high and low tide
        tide_high = df.query('is_high_tide==1')['water_level']
        tide_low = df.query('is_high_tide==0')['water_level']

        # Create summary statistics
        high_statistics = tide_high.agg(['mean', 'median', IQR])
        low_statistics = tide_low.agg(['mean', 'median', IQR])

        # Calculate ratio of high tide days
        all_high_days = df.query('is_high_tide==1').groupby('year').count()['water_level']

        high_days = df.query(f'(water_level>{tide_high.quantile(.75)}) & (is_high_tide==1)').groupby('year').count()['water_level']

        high_ratio = (high_days/all_high_days).reset_index()

        # Calculate ratio of low tide days
        all_low_days = df.query('is_high_tide==0').groupby('year').count()['water_level']

        low_days = df.query(f'(water_level<{tide_low.quantile(.25)}) & (is_high_tide==0)').groupby('year').count()['water_level']

        low_ratio = (low_days/all_low_days).reset_index()

        solution = {
            'high_statistics': high_statistics,
            'low_statistics': low_statistics,
            'high_ratio': high_ratio,
            'low_ratio':low_ratio,
            'raw_data':df        
        }
        
    except:
        solution = 0

    return solution

In [4]:
# run tidal_stats function for all datasets along the Thames:

# Get filenames for all Thames data

filenames = [
    'London_Bridge.txt',
    'All_Hallows_Pier.txt',
    'Temple_Pier.txt',
    'Strand_on_Green.txt',
    'Richmond.txt',
    'Walton_on_Naze.txt',
    'Margate.txt',
    'Shivering_Sand.txt',
    'Southend.txt',
    'Coryton.txt',
    'Tilbury.txt',
    'Silvertown.txt',
    'Cherry_Garden_Pier.txt',  
]

# create list to store the resulting tidal statistics:

results_dict = {}

for dataset in filenames:
    results_dict[dataset.replace('.txt',"").replace('_'," ")] = tidal_stats(dataset)

In [132]:
# creating merged df for all raw data

# initializing an empty dataframe that will store merged data
thames_data = pd.DataFrame()

# for loop to populate the merged dataframe and add a 'Location' column for each tidal location
for key in list(results_dict.keys()):
    df = results_dict[key]['raw_data']
    df['Location'] = key
    thames_data = pd.concat([df, thames_data], sort=False)
        

In [94]:
import pandas as pd
from sklearn.ensemble import IsolationForest

data = thames_data[thames_data['Location'] == 'London Bridge']['water_level']

# Drop any rows with missing values
data.dropna(inplace=True)

# Convert the Series to a DataFrame with a single column named "WaterLevel"
df = pd.DataFrame({'WaterLevel': data})

# Extract the "WaterLevel" column
X = df['WaterLevel'].values.reshape(-1, 1)

# Train the Isolation Forest model
clf = IsolationForest(n_estimators=100, max_samples='auto', contamination=0.001, max_features=1.0, bootstrap=False, random_state=42)
clf.fit(X)

# Predict outliers
df['is_outlier'] = clf.predict(X)
df['is_outlier'] = df['is_outlier'].map({1: 0, -1: 1})  # Convert 1 to 0 and -1 to 1 for anomaly labels

# Print anomalies
anomalies = df[df['is_outlier'] == 1]
print(anomalies)


/var/folders/82/2cp5z8p14d3250cjgg9g2yqh0000gn/T/ipykernel_14751/701171619.py:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  data.dropna(inplace=True)


        WaterLevel  is_outlier
11079      -3.4241           1
13656      -3.4495           1
21723       5.2115           1
24049      -3.4241           1
24173      -3.6019           1
...            ...         ...
113028     -3.4700           1
113998     -3.4500           1
114110     -3.5000           1
114112     -3.5800           1
114212     -3.5500           1

[108 rows x 2 columns]


In [95]:
# merging on the index to bring in the is_outlier column from the model output
df_lbridge = thames_data[thames_data['Location'] == 'London Bridge'].merge(df['is_outlier'], how='left',left_index=True, right_index=True)

In [135]:
from bokeh.plotting import figure, show
from bokeh.models import ColumnDataSource, HoverTool, DatetimeTickFormatter, Legend
from bokeh.io import output_notebook

# Convert datetime column to proper datetime format
df_lbridge['datetime'] = pd.to_datetime(df_lbridge['datetime'])

# Create a ColumnDataSource for average high tide
source_high_tide = ColumnDataSource(df_lbridge[df_lbridge['is_high_tide'] == 1])

# Create a ColumnDataSource for average low tide
source_low_tide = ColumnDataSource(df_lbridge[df_lbridge['is_high_tide'] == 0])

# Create a ColumnDataSource for anomalies
source_anomalies = ColumnDataSource(df_lbridge[df_lbridge['is_outlier'] == 1])

# Create a figure
p = figure(title="Water level anomalies detected at London Bridge (1911-1995), using Isolation Forest", x_axis_label='Date', y_axis_label='Water Level')

# Plot the average high tide as a line
line_high_tide = p.line(x='datetime', y='water_level', source=source_high_tide, line_color='navy')

# Plot the average low tide as a line
line_low_tide = p.line(x='datetime', y='water_level', source=source_low_tide, line_color='skyblue')

# Plot the anomalies as markers
circle_anomalies = p.circle(x='datetime', y='water_level', source=source_anomalies, size=8, fill_color='red', line_color='black', name='anomaly')

# Add a hover tool to show additional information
hover = HoverTool(names=['anomaly'])
hover.tooltips = [('Date', '@datetime{%Y-%m-%d}'), ('Water Level', '@water_level{0.00}m')]
hover.formatters = {'@datetime': 'datetime'}
p.add_tools(hover)

# Update x-axis ticker to show date as regular format
p.xaxis.formatter = DatetimeTickFormatter(days='%Y-%m-%d')

# Create a legend and add it to the plot
legend = Legend(items=[('High Tide', [line_high_tide]), ('Low Tide', [line_low_tide]), ('Anomaly', [circle_anomalies])], location='top_center')
p.add_layout(legend, 'below')

# Show the plot
output_notebook()
show(p)


Loading BokehJS ...